<a href="https://colab.research.google.com/github/cfonderson/portfolio/blob/main/DS4A%20Capstone/data_ingestion.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# DS4A CAPSTONE PROJECT: DATA INGESTION AND CLEANING
__Team Members: Cynthia Fonderson, Gabriel Briones, Solomon Berhe, Moradeke Adeniji-Somefun__

In [ ]:
import sys
import json
import requests 
import numpy as np
import pandas as pd 

# Change view settings
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

# Access the census api key
df = pd.read_csv('api_keys.csv')
census_api_key = df.loc[df['API'] == 'census']['KEY'].iloc[0]

## Importing pregnancy-related mortality data for select populations from 2015 to 2019 

Description: Pregnancy-related mortality data from the United States from 2015 to 2019. Data was aggregated by state and race. All underlying causes of death were considered for this project.

Source: CDC Wonder, Multiple Cause of Death Mortality Database

In [ ]:
cdc = pd.read_csv("Pregnancy-related mortality by state and race from 2015-2019.txt", delimiter='\t')
cdc

Notes                 State  \
0                                                  NaN               Alabama   
1                                                  NaN               Alabama   
2                                                  NaN               Alabama   
3                                                  NaN               Alabama   
4                                                  NaN                Alaska   
5                                                  NaN                Alaska   
6                                                  NaN                Alaska   
7                                                  NaN                Alaska   
8                                                  NaN               Arizona   
9                                                  NaN               Arizona   
10                                                 NaN               Arizona   
11                                                 NaN               Arizona   
12                                                 NaN              Arkansas   
13                                                 NaN              Arkansas   
14                                                 NaN              Arkansas   
15                                                 NaN              Arkansas   
16                                                 NaN            California   
17                                                 NaN            California   
18                                                 NaN            California   
19                                                 NaN            California   
20                                                 NaN              Colorado   
21                                                 NaN              Colorado   
22                                                 NaN              Colorado   
23                                                 NaN              Colorado   
24                                                 NaN           Connecticut   
25                                                 NaN           Connecticut   
26                                                 NaN           Connecticut   
27                                                 NaN           Connecticut   
28                                                 NaN              Delaware   
29                                                 NaN              Delaware   
30                                                 NaN              Delaware   
31                                                 NaN              Delaware   
32                                                 NaN  District of Columbia   
33                                                 NaN  District of Columbia   
34                                                 NaN  District of Columbia   
35                                                 NaN  District of Columbia   
36                                                 NaN               Florida   
37                                                 NaN               Florida   
38                                                 NaN               Florida   
39                                                 NaN               Florida   
40                                                 NaN               Georgia   
41                                                 NaN               Georgia   
42                                                 NaN               Georgia   
43                                                 NaN               Georgia   
44                                                 NaN                Hawaii   
45                                                 NaN                Hawaii   
46                                                 NaN                Hawaii   
47                                                 NaN                Hawaii   
48                                                 NaN                 Idaho   
49                                               

In [ ]:
# dropping unnecesary columns
cdc.drop(['Notes','State Code','Race Code','Population'], 
         axis = 1, inplace = True)

cdc.head()

State                              Race      Deaths  Crude Rate  \
0  Alabama  American Indian or Alaska Native  Suppressed  Suppressed   
1  Alabama         Asian or Pacific Islander  Suppressed  Suppressed   
2  Alabama         Black or African American         124         1.5   
3  Alabama                             White         137         0.7   
4   Alaska  American Indian or Alaska Native          10  Unreliable   

  Age Adjusted Rate  
0        Suppressed  
1        Suppressed  
2               1.6  
3               0.8  
4        Unreliable

In [ ]:
# renaming columns 
cdc.columns = cdc.columns.str.lower().str.replace(' ', '_').str.replace('adjusted', 'adj')

cdc.head()

state                              race      deaths  crude_rate  \
0  Alabama  American Indian or Alaska Native  Suppressed  Suppressed   
1  Alabama         Asian or Pacific Islander  Suppressed  Suppressed   
2  Alabama         Black or African American         124         1.5   
3  Alabama                             White         137         0.7   
4   Alaska  American Indian or Alaska Native          10  Unreliable   

  age_adj_rate  
0   Suppressed  
1   Suppressed  
2          1.6  
3          0.8  
4   Unreliable

In [ ]:
# converting suppressed and unreliable values to Nan 
cols = ['deaths','crude_rate','age_adj_rate']
for col in cols:
    cdc[col] = cdc[col].apply(lambda x : np.nan if x == ('Suppressed') else x)
    cdc[col] = cdc[col].apply(lambda x : np.nan if x == ('Unreliable') else x)

cdc

state                              race deaths crude_rate  \
0                 Alabama  American Indian or Alaska Native    NaN        NaN   
1                 Alabama         Asian or Pacific Islander    NaN        NaN   
2                 Alabama         Black or African American    124        1.5   
3                 Alabama                             White    137        0.7   
4                  Alaska  American Indian or Alaska Native     10        NaN   
5                  Alaska         Asian or Pacific Islander    NaN        NaN   
6                  Alaska         Black or African American    NaN        NaN   
7                  Alaska                             White    NaN        NaN   
8                 Arizona  American Indian or Alaska Native     31        1.3   
9                 Arizona         Asian or Pacific Islander    NaN        NaN   
10                Arizona         Black or African American     33        1.3   
11                Arizona                             White    176        0.5   
12               Arkansas  American Indian or Alaska Native    NaN        NaN   
13               Arkansas         Asian or Pacific Islander    NaN        NaN   
14               Arkansas         Black or African American     47        1.6   
15               Arkansas                             White     82        0.6   
16             California  American Indian or Alaska Native    NaN        NaN   
17             California         Asian or Pacific Islander     83        0.2   
18             California         Black or African American    115        0.7   
19             California                             White    472        0.3   
20               Colorado  American Indian or Alaska Native    NaN        NaN   
21               Colorado         Asian or Pacific Islander    NaN        NaN   
22               Colorado         Black or African American     17        NaN   
23               Colorado                             White    118        0.4   
24            Connecticut  American Indian or Alaska Native    NaN        NaN   
25            Connecticut         Asian or Pacific Islander    NaN        NaN   
26            Connecticut         Black or African American     18        NaN   
27            Connecticut                             White     40        0.2   
28               Delaware  American Indian or Alaska Native    NaN        NaN   
29               Delaware         Asian or Pacific Islander    NaN        NaN   
30               Delaware         Black or African American     15        NaN   
31               Delaware                             White     11        NaN   
32   District of Columbia  American Indian or Alaska Native    NaN        NaN   
33   District of Columbia         Asian or Pacific Islander    NaN        NaN   
34   District of Columbia         Black or African American     21        1.0   
35   District of Columbia                             White    NaN        NaN   
36                Florida  American Indian or Alaska Native    NaN        NaN   
37                Florida         Asian or Pacific Islander     11        NaN   
38                Florida         Black or African American    181        0.8   
39                Florida                             White    323        0.3   
40                Georgia  American Indian or Alaska Native    NaN        NaN   
41                Georgia         Asian or Pacific Islander     18        NaN   
42                Georgia         Black or African American    326        1.6   
43                Georgia                             White    274        0.7   
44                 Hawaii  American Indian or Alaska Native    NaN        NaN   
45                 Hawaii         Asian or Pacific Islander     25        0.4   
46                 Hawaii         Black or African American    NaN        NaN   
47                 Hawaii                             White    NaN        NaN   
48                  Idaho  American Indian or Alask

In [ ]:
# assigning appropriate data types
cdc['state'] = cdc['state'].astype('category')
cdc['race'] = cdc['race'].astype('category')
cdc['deaths'] = cdc['deaths'].astype('float')
cdc['crude_rate'] = cdc['crude_rate'].astype('float')
cdc['age_adj_rate'] = cdc['age_adj_rate'].astype('float')

cdc.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 272 entries, 0 to 271
Data columns (total 5 columns):
 #   Column        Non-Null Count  Dtype   
---  ------        --------------  -----   
 0   state         204 non-null    category
 1   race          204 non-null    category
 2   deaths        100 non-null    float64 
 3   crude_rate    76 non-null     float64 
 4   age_adj_rate  76 non-null     float64 
dtypes: category(2), float64(3)
memory usage: 9.7 KB


In [ ]:
df1 = cdc.groupby(['state','race'])[['deaths',
                                     'crude_rate',
                                     'age_adj_rate']].mean().copy().reset_index()
df1

state                              race  deaths  \
0                 Alabama  American Indian or Alaska Native     NaN   
1                 Alabama         Asian or Pacific Islander     NaN   
2                 Alabama         Black or African American   124.0   
3                 Alabama                             White   137.0   
4                  Alaska  American Indian or Alaska Native    10.0   
5                  Alaska         Asian or Pacific Islander     NaN   
6                  Alaska         Black or African American     NaN   
7                  Alaska                             White     NaN   
8                 Arizona  American Indian or Alaska Native    31.0   
9                 Arizona         Asian or Pacific Islander     NaN   
10                Arizona         Black or African American    33.0   
11                Arizona                             White   176.0   
12               Arkansas  American Indian or Alaska Native     NaN   
13               Arkansas         Asian or Pacific Islander     NaN   
14               Arkansas         Black or African American    47.0   
15               Arkansas                             White    82.0   
16             California  American Indian or Alaska Native     NaN   
17             California         Asian or Pacific Islander    83.0   
18             California         Black or African American   115.0   
19             California                             White   472.0   
20               Colorado  American Indian or Alaska Native     NaN   
21               Colorado         Asian or Pacific Islander     NaN   
22               Colorado         Black or African American    17.0   
23               Colorado                             White   118.0   
24            Connecticut  American Indian or Alaska Native     NaN   
25            Connecticut         Asian or Pacific Islander     NaN   
26            Connecticut         Black or African American    18.0   
27            Connecticut                             White    40.0   
28               Delaware  American Indian or Alaska Native     NaN   
29               Delaware         Asian or Pacific Islander     NaN   
30               Delaware         Black or African American    15.0   
31               Delaware                             White    11.0   
32   District of Columbia  American Indian or Alaska Native     NaN   
33   District of Columbia         Asian or Pacific Islander     NaN   
34   District of Columbia         Black or African American    21.0   
35   District of Columbia                             White     NaN   
36                Florida  American Indian or Alaska Native     NaN   
37                Florida         Asian or Pacific Islander    11.0   
38                Florida         Black or African American   181.0   
39                Florida                             White   323.0   
40                Georgia  American Indian or Alaska Native     NaN   
41                Georgia         Asian or Pacific Islander    18.0   
42                Georgia         Black or African American   326.0   
43                Georgia                             White   274.0   
44                 Hawaii  American Indian or Alaska Native     NaN   
45                 Hawaii         Asian or Pacific Islander    25.0   
46                 Hawaii         Black or African American     NaN   
47                 Hawaii                             White     NaN   
48                  Idaho  American Indian or Alaska Native     NaN   
49                  Idaho         Asian or Pacific Islander     NaN   
50                  Idaho         Black or African American     NaN   
51                  Idaho                             White    48.0   
52               Illinois  American Indian or Alaska Native     NaN   
53               Illinois         Asian or Pacific Islander     NaN   
54               Illinois         Black or African American    92.0   
55               Illinois                   

In [ ]:
df1.shape

(204, 5)

In [ ]:
df1.to_csv('mortality_data.csv', index=False)

## Importing socio-economic data for select female populations in the USA from 2015 to 2019

Description: Socio-economic factors that affect female health in the United States from 2015 to 2019. Selected demographic data includes citizenship/immigration status, marital status, fertility, educational attainment, employment status, income and access to healthcare.

Source: U.S. Census, American Community Survey

||Variable|Identifier|Type|Description|
|:---:|:--------:|:------:|:---:|:------------|
|01|state|NAME|STRING|U.S. state name|
|02|race|POPGROUP_TTL(LABEL)|STRING|Race category|
|03|pop_over18|S0201_(0)026E|INTEGER|Total Population, 18 years and over|
|04|fper_over18|S0201_(0)028E|FLOAT|Percentage of female population, 18 years and over|
|05|pop_over65|S0201_(0)035E|INTEGER|Total Population, 65 years and over|
|06|fper_over65|S0201_(0)037E|FLOAT|Percentage of female population, 65 years and over|
|07|fpop_over15|S0201_(0)072E|INTEGER|Population of women, 15 years and over|
|08|per_married|S0201_(0)073E|FLOAT|Percentage of women, 15 years and over, now married|
|09|per_widowed|S0201_(0)074E|FLOAT|Percentage of women, 15 years and over, widowed|
|10|per_divorced|S0201_(0)075E|FLOAT|Percentage of women, 15 years and over, divorced|
|11|per_separated|S0201_(0)076E|FLOAT|Percentage of women, 15 years and over, separated|
|12|per_never_mar|S0201_(0)077E|FLOAT|Percentage of women, 15 years and over, never married|
|13|pop_over25|S0201_(0)090E|INTEGER|Total population, 25 years and over|
|14|fper_hs_diploma|S0201_(0)098E|FLOAT|Percentage of female population, 25 years and over, with a high school diploma or higher|
|15|fper_higher_ed|S0201_(0)101E|FLOAT|Percentage of female population, 25 years and over, with a bachelor's degree or higher|
|16|fertility|S0201_(0)103E|INTEGER|Population, 15 to 50 years, who gave birth in the past year|
|17|fertility_um|S0201_(0)104E|INTEGER|Population of unmarried women, 15 to 50 years, who gave birth in the past year 
|18|native_pop|S0201_(0)127E|INTEGER|Population of native U.S. citizens|
|19|native_fper|S0201_(0)129E|FLOAT|Percentage of female native U.S. citizens|
|20|foreign_pop|S0201_(0)130E|INTEGER|Population of foreign-born U.S. residents|
|21|foreign_fper|S0201_(0)132E|FLOAT|Percentage of female foreign-born U.S. residents|
|22|foreign_cit_pop|S0201_(0)133E|INTEGER|Population of foreign-born U.S. citizens|
|23|foreign_cit_fper|S0201_(0)135E|FLOAT|Percentage of female foreign-born U.S. citizens|
|24|foreign_imm_pop|S0201_(0)136E|INTEGER|Population of foreign-born U.S. immigrants|
|25|foreign_imm_fper|S0201_(0)138E|FLOAT|Percentage of female foreign-born U.S. immigrants|
|26|pop_over16|S0201_(0)162E|INTEGER|Population of females, 16 years and over|
|27|labor_force_f|S0201_(0)164E|FLOAT|Percentage of females, 16 years and over, in the labor force|
|28|employed_f|S0201_(0)165E|FLOAT|Percentage of females, 16 years and over, employed|
|29|unemployed_f|S0201_(0)166E|FLOAT|Percentage of females, 16 years and over, unemployed|
|30|family_income_mc|S0201_(0)227E|INTEGER|Median inflation-adjusted income for married couples|
|31|family_income_um|S0201_(0)231E|INTERGER|Median inflation-adjusted income for female householders|
|32|mean_income_f|S0201_(0)239E|INTEGER|Mean income for female full-time, year-round workers|
|33|med_income_f|S0201_(0)241E|INTEGER|Median income for female full-time, year-round workers|
|34|population|S0201_(0)242E|INTEGER|Civilian, noninstitionalized population|
|35|insurance_private|S0201_(0)243E|FLOAT|Percentage of people in the selected group with private health coverage|
|36|insurance_public|S0201_(0)244E|FLOAT|Percentage of people in the selected group with public health coverage|
|37|insurance_none|S0201_(0)245E|FLOAT|Percentage of people in the selected group with no health coverage|
|38|pr_married|S0201_(0)249E|FLOAT|Poverty rates for families with married couples|
|39|pr_married_kid|S0201_(0)250E|FLOAT|Poverty rates for families with married couples and children under 18|
|40|pr_unmarriedf|S0201_(0)252E|FLOAT|Poverty rates for families with a female householder (no spouse)|
|41|pr_unmarriedf_kid|S0201_(0)253E|FLOAT|Poverty rates for families with a female householder (no spouse) and children under 18|
|42|race_code|POPGROUP|INTEGER|Race code|
|43|state_code|state|STRING|U.S. state code|
|44|year|year|INTEGER|Census Year|

In [ ]:
# Call 1: demographics for selected populations of women by state for 2015
    
# Race = White 
url_1 = 'http://api.census.gov/data/2015/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=002&key={0}'\
          .format(census_api_key)

# Race = Black 
url_2 = 'https://api.census.gov/data/2015/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=004&key={0}'\
          .format(census_api_key)

# Race = American Indian and Alaska Native alone   
url_3 = 'https://api.census.gov/data/2015/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=006&key={0}'\
          .format(census_api_key)

# Race = Asian 
url_4 = 'https://api.census.gov/data/2015/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=012&key={0}'\
          .format(census_api_key)

# Race = Native Hawaiian and other Pacific Islander alone 
url_5 = 'https://api.census.gov/data/2015/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=050&key={0}'\
          .format(census_api_key)

urls = [url_1,url_2,url_3,url_4,url_5]

dfs = []
for url in urls:
    try:
        response = requests.get(url)
        response.raise_for_status()
    except requests.exceptions.RequestException as e:
        print(e, file=sys.stderr)
    cols = response.json()[0]
    recs = response.json()[1:]
    data = pd.DataFrame(recs, columns=cols)
    dfs.append(data)
    
data_2015 = pd.concat(dfs, ignore_index=True)
data_2015['year'] = 2015
data_2015.rename(columns={'POPGROUP_TTL':'RACE'},inplace= True)
data_2015

NAME                                               RACE  \
0             Mississippi                                        White alone   
1                Missouri                                        White alone   
2                 Montana                                        White alone   
3                Nebraska                                        White alone   
4                  Nevada                                        White alone   
5           New Hampshire                                        White alone   
6              New Jersey                                        White alone   
7              New Mexico                                        White alone   
8                New York                                        White alone   
9          North Carolina                                        White alone   
10           North Dakota                                        White alone   
11                   Ohio                                        White alone   
12               Oklahoma                                        White alone   
13                 Oregon                                        White alone   
14         South Carolina                                        White alone   
15           South Dakota                                        White alone   
16              Tennessee                                        White alone   
17           Pennsylvania                                        White alone   
18           Rhode Island                                        White alone   
19                   Utah                                        White alone   
20                  Texas                                        White alone   
21                Vermont                                        White alone   
22               Virginia                                        White alone   
23             Washington                                        White alone   
24          West Virginia                                        White alone   
25              Wisconsin                                        White alone   
26                Arizona                                        White alone   
27                Wyoming                                        White alone   
28                Alabama                                        White alone   
29                 Alaska                                        White alone   
30               Arkansas                                        White alone   
31                 Hawaii                                        White alone   
32                Georgia                                        White alone   
33             California                                        White alone   
34               Colorado                                        White alone   
35               Delaware                                        White alone   
36            Connecticut                                        White alone   
37   District of Columbia                                        White alone   
38                Florida                                        White alone   
39                  Idaho                                        White alone   
40               Illinois                                        White alone   
41                Indiana                                        White alone   
42                   Iowa                                        White alone   
43                 Kansas                                        White alone   
44               Kentucky                                        White alone   
45              Louisiana                                        White alone   
46                  Maine                                        White alone   
47               Michigan                                        White alone   
48              Minnesota                                        White alone   
49               Mary

In [ ]:
# Call 2: demographics for selected populations of women by state for 2016

# Race = White 
url_1 = 'https://api.census.gov/data/2016/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_0026E,S0201_0028E,'\
          'S0201_0035E,S0201_0037E,S0201_0072E,S0201_0073E,'\
          'S0201_0074E,S0201_0075E,S0201_0076E,S0201_0077E,'\
          'S0201_0090E,S0201_0098E,S0201_0101E,S0201_0103E,'\
          'S0201_0104E,S0201_0127E,S0201_0129E,S0201_0130E,'\
          'S0201_0132E,S0201_0133E,S0201_0135E,S0201_0136E,'\
          'S0201_0138E,S0201_0162E,S0201_0164E,S0201_0165E,'\
          'S0201_0166E,S0201_0227E,S0201_0231E,S0201_0239E,'\
          'S0201_0241E,S0201_0242E,S0201_0243E,S0201_0244E,'\
          'S0201_0245E,S0201_0249E,S0201_0250E,S0201_0252E,'\
          'S0201_0253E&for=state:*&POPGROUP=002&key={0}'\
          .format(census_api_key)

# Race = Black 
url_2 = 'https://api.census.gov/data/2016/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_0026E,S0201_0028E,'\
          'S0201_0035E,S0201_0037E,S0201_0072E,S0201_0073E,'\
          'S0201_0074E,S0201_0075E,S0201_0076E,S0201_0077E,'\
          'S0201_0090E,S0201_0098E,S0201_0101E,S0201_0103E,'\
          'S0201_0104E,S0201_0127E,S0201_0129E,S0201_0130E,'\
          'S0201_0132E,S0201_0133E,S0201_0135E,S0201_0136E,'\
          'S0201_0138E,S0201_0162E,S0201_0164E,S0201_0165E,'\
          'S0201_0166E,S0201_0227E,S0201_0231E,S0201_0239E,'\
          'S0201_0241E,S0201_0242E,S0201_0243E,S0201_0244E,'\
          'S0201_0245E,S0201_0249E,S0201_0250E,S0201_0252E,'\
          'S0201_0253E&for=state:*&POPGROUP=004&key={0}'\
          .format(census_api_key)

# Race = American Indian and Alaska Native alone   
url_3 = 'https://api.census.gov/data/2016/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_0026E,S0201_0028E,'\
          'S0201_0035E,S0201_0037E,S0201_0072E,S0201_0073E,'\
          'S0201_0074E,S0201_0075E,S0201_0076E,S0201_0077E,'\
          'S0201_0090E,S0201_0098E,S0201_0101E,S0201_0103E,'\
          'S0201_0104E,S0201_0127E,S0201_0129E,S0201_0130E,'\
          'S0201_0132E,S0201_0133E,S0201_0135E,S0201_0136E,'\
          'S0201_0138E,S0201_0162E,S0201_0164E,S0201_0165E,'\
          'S0201_0166E,S0201_0227E,S0201_0231E,S0201_0239E,'\
          'S0201_0241E,S0201_0242E,S0201_0243E,S0201_0244E,'\
          'S0201_0245E,S0201_0249E,S0201_0250E,S0201_0252E,'\
          'S0201_0253E&for=state:*&POPGROUP=006&key={0}'\
          .format(census_api_key)

# Race = Asian 
url_4 = 'https://api.census.gov/data/2016/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_0026E,S0201_0028E,'\
          'S0201_0035E,S0201_0037E,S0201_0072E,S0201_0073E,'\
          'S0201_0074E,S0201_0075E,S0201_0076E,S0201_0077E,'\
          'S0201_0090E,S0201_0098E,S0201_0101E,S0201_0103E,'\
          'S0201_0104E,S0201_0127E,S0201_0129E,S0201_0130E,'\
          'S0201_0132E,S0201_0133E,S0201_0135E,S0201_0136E,'\
          'S0201_0138E,S0201_0162E,S0201_0164E,S0201_0165E,'\
          'S0201_0166E,S0201_0227E,S0201_0231E,S0201_0239E,'\
          'S0201_0241E,S0201_0242E,S0201_0243E,S0201_0244E,'\
          'S0201_0245E,S0201_0249E,S0201_0250E,S0201_0252E,'\
          'S0201_0253E&for=state:*&POPGROUP=012&key={0}'\
          .format(census_api_key)

# Race = Native Hawaiian and other Pacific Islander alone 
url_5 = 'https://api.census.gov/data/2016/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_0026E,S0201_0028E,'\
          'S0201_0035E,S0201_0037E,S0201_0072E,S0201_0073E,'\
          'S0201_0074E,S0201_0075E,S0201_0076E,S0201_0077E,'\
          'S0201_0090E,S0201_0098E,S0201_0101E,S0201_0103E,'\
          'S0201_0104E,S0201_0127E,S0201_0129E,S0201_0130E,'\
          'S0201_0132E,S0201_0133E,S0201_0135E,S0201_0136E,'\
          'S0201_0138E,S0201_0162E,S0201_0164E,S0201_0165E,'\
          'S0201_0166E,S0201_0227E,S0201_0231E,S0201_0239E,'\
          'S0201_0241E,S0201_0242E,S0201_0243E,S0201_0244E,'\
          'S0201_0245E,S0201_0249E,S0201_0250E,S0201_0252E,'\
          'S0201_0253E&for=state:*&POPGROUP=050&key={0}'\
          .format(census_api_key)

urls = [url_1,url_2,url_3,url_4,url_5]

dfs = []
for url in urls:
    try:
        response = requests.get(url)
        response.raise_for_status()
    except requests.exceptions.RequestException as e:
        print(e, file=sys.stderr)
    cols = response.json()[0]
    recs = response.json()[1:]
    data = pd.DataFrame(recs, columns=cols)
    dfs.append(data)
    
data_2016 = pd.concat(dfs, ignore_index=True)
data_2016['year'] = 2016
data_2016.rename(columns={'POPGROUP_TTL':'RACE',
                          'S0201_0026E':'S0201_026E','S0201_0028E':'S0201_028E',
                          'S0201_0035E':'S0201_035E','S0201_0037E':'S0201_037E',
                          'S0201_0072E':'S0201_072E','S0201_0073E':'S0201_073E',
                          'S0201_0074E':'S0201_074E','S0201_0075E':'S0201_075E',
                          'S0201_0076E':'S0201_076E','S0201_0077E':'S0201_077E',
                          'S0201_0090E':'S0201_090E','S0201_0098E':'S0201_098E',
                          'S0201_0101E':'S0201_101E','S0201_0103E':'S0201_103E',
                          'S0201_0104E':'S0201_104E','S0201_0127E':'S0201_127E',
                          'S0201_0129E':'S0201_129E','S0201_0130E':'S0201_130E',
                          'S0201_0132E':'S0201_132E','S0201_0133E':'S0201_133E',
                          'S0201_0135E':'S0201_135E','S0201_0136E':'S0201_136E',
                          'S0201_0138E':'S0201_138E','S0201_0162E':'S0201_162E',
                          'S0201_0164E':'S0201_164E','S0201_0165E':'S0201_165E',
                          'S0201_0166E':'S0201_166E','S0201_0227E':'S0201_227E',
                          'S0201_0231E':'S0201_231E','S0201_0239E':'S0201_239E',
                          'S0201_0241E':'S0201_241E','S0201_0242E':'S0201_242E',
                          'S0201_0243E':'S0201_243E','S0201_0244E':'S0201_244E',
                          'S0201_0245E':'S0201_245E','S0201_0249E':'S0201_249E',
                          'S0201_0250E':'S0201_250E','S0201_0252E':'S0201_252E',
                          'S0201_0253E':'S0201_253E'}, inplace= True)
data_2016

NAME                                               RACE  \
0           New Hampshire                                        White alone   
1               Tennessee                                        White alone   
2           West Virginia                                        White alone   
3               Wisconsin                                        White alone   
4                  Oregon                                        White alone   
5                 Alabama                                        White alone   
6                  Alaska                                        White alone   
7                 Vermont                                        White alone   
8                 Arizona                                        White alone   
9                Arkansas                                        White alone   
10             California                                        White alone   
11               New York                                        White alone   
12               Colorado                                        White alone   
13            Connecticut                                        White alone   
14         South Carolina                                        White alone   
15               Delaware                                        White alone   
16   District of Columbia                                        White alone   
17                Florida                                        White alone   
18                Georgia                                        White alone   
19                 Hawaii                                        White alone   
20                  Idaho                                        White alone   
21               Illinois                                        White alone   
22                Indiana                                        White alone   
23                   Iowa                                        White alone   
24                 Kansas                                        White alone   
25               Kentucky                                        White alone   
26              Louisiana                                        White alone   
27                  Maine                                        White alone   
28               Maryland                                        White alone   
29          Massachusetts                                        White alone   
30               Michigan                                        White alone   
31              Minnesota                                        White alone   
32            Mississippi                                        White alone   
33               Missouri                                        White alone   
34                Montana                                        White alone   
35               Nebraska                                        White alone   
36                 Nevada                                        White alone   
37             New Jersey                                        White alone   
38             New Mexico                                        White alone   
39         North Carolina                                        White alone   
40           North Dakota                                        White alone   
41                   Ohio                                        White alone   
42               Oklahoma                                        White alone   
43           Pennsylvania                                        White alone   
44           Rhode Island                                        White alone   
45           South Dakota                                        White alone   
46                  Texas                                        White alone   
47                   Utah                                        White alone   
48               Virginia                                        White alone   
49             Washin

In [ ]:
# Call 3: demographics for selected populations of women by state for 2017

# Race = White 
url_1 = 'http://api.census.gov/data/2017/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=002&key={0}'\
          .format(census_api_key)

# Race = Black 
url_2 = 'https://api.census.gov/data/2017/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=004&key={0}'\
          .format(census_api_key)

# Race = American Indian and Alaska Native alone   
url_3 = 'https://api.census.gov/data/2017/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=006&key={0}'\
          .format(census_api_key)

# Race = Asian 
url_4 = 'https://api.census.gov/data/2017/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=012&key={0}'\
          .format(census_api_key)

# Race = Native Hawaiian and other Pacific Islander alone 
url_5 = 'https://api.census.gov/data/2017/acs/acs1/spp?'\
          'get=NAME,POPGROUP_TTL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=050&key={0}'\
          .format(census_api_key)

urls = [url_1,url_2,url_3,url_4,url_5]

dfs = []
for url in urls:
    try:
        response = requests.get(url)
        response.raise_for_status()
    except requests.exceptions.RequestException as e:
        print(e, file=sys.stderr)
    cols = response.json()[0]
    recs = response.json()[1:]
    data = pd.DataFrame(recs, columns=cols)
    dfs.append(data)
    
data_2017 = pd.concat(dfs, ignore_index=True)
data_2017['year'] = 2017
data_2017.rename(columns={'POPGROUP_TTL':'RACE'},inplace= True)
data_2017

NAME                                               RACE  \
0               Tennessee                                        White alone   
1                 Alabama                                        White alone   
2                  Alaska                                        White alone   
3               Louisiana                                        White alone   
4                 Arizona                                        White alone   
5                Arkansas                                        White alone   
6              California                                        White alone   
7                Colorado                                        White alone   
8             Connecticut                                        White alone   
9                Delaware                                        White alone   
10   District of Columbia                                        White alone   
11                Florida                                        White alone   
12                Georgia                                        White alone   
13                 Hawaii                                        White alone   
14                  Idaho                                        White alone   
15               Illinois                                        White alone   
16                Indiana                                        White alone   
17                   Iowa                                        White alone   
18                 Kansas                                        White alone   
19               Kentucky                                        White alone   
20                  Maine                                        White alone   
21               Maryland                                        White alone   
22          Massachusetts                                        White alone   
23           Rhode Island                                        White alone   
24               Michigan                                        White alone   
25              Minnesota                                        White alone   
26            Mississippi                                        White alone   
27               Missouri                                        White alone   
28                Montana                                        White alone   
29               Nebraska                                        White alone   
30                 Nevada                                        White alone   
31          New Hampshire                                        White alone   
32             New Jersey                                        White alone   
33             New Mexico                                        White alone   
34               New York                                        White alone   
35         North Carolina                                        White alone   
36           North Dakota                                        White alone   
37                   Ohio                                        White alone   
38               Oklahoma                                        White alone   
39                 Oregon                                        White alone   
40           Pennsylvania                                        White alone   
41         South Carolina                                        White alone   
42           South Dakota                                        White alone   
43                  Texas                                        White alone   
44                   Utah                                        White alone   
45                Vermont                                        White alone   
46               Virginia                                        White alone   
47             Washington                                        White alone   
48          West Virginia                                        White alone   
49              Wisco

In [ ]:
# Call 4: demographics for selected populations of women by state for 2018

# Race = White 
url_1 = 'https://api.census.gov/data/2018/acs/acs1/spp?'\
          'get=NAME,POPGROUP_LABEL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=002&key={0}'\
          .format(census_api_key)

# Race = Black 
url_2 = 'https://api.census.gov/data/2018/acs/acs1/spp?'\
          'get=NAME,POPGROUP_LABEL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=004&key={0}'\
          .format(census_api_key)

# Race = American Indian and Alaska Native alone   
url_3 = 'https://api.census.gov/data/2018/acs/acs1/spp?'\
          'get=NAME,POPGROUP_LABEL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=006&key={0}'\
          .format(census_api_key)

# Race = Asian 
url_4 = 'https://api.census.gov/data/2018/acs/acs1/spp?'\
          'get=NAME,POPGROUP_LABEL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=012&key={0}'\
          .format(census_api_key)

# Race = Native Hawaiian and other Pacific Islander alone 
url_5 = 'https://api.census.gov/data/2018/acs/acs1/spp?'\
          'get=NAME,POPGROUP_LABEL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=050&key={0}'\
          .format(census_api_key)

urls = [url_1,url_2,url_3,url_4,url_5]

dfs = []
for url in urls:
    try:
        response = requests.get(url)
        response.raise_for_status()
    except requests.exceptions.RequestException as e:
        print(e, file=sys.stderr)
    cols = response.json()[0]
    recs = response.json()[1:]
    data = pd.DataFrame(recs, columns=cols)
    dfs.append(data)
    
data_2018 = pd.concat(dfs, ignore_index=True)
data_2018['year'] = 2018
data_2018.rename(columns={'POPGROUP_LABEL':'RACE'},inplace= True)
data_2018

NAME                                               RACE  \
0               Wisconsin                                        White alone   
1                 Wyoming                                        White alone   
2             Mississippi                                        White alone   
3                Missouri                                        White alone   
4                 Montana                                        White alone   
5                Nebraska                                        White alone   
6            South Dakota                                        White alone   
7                  Nevada                                        White alone   
8           New Hampshire                                        White alone   
9              New Jersey                                        White alone   
10             New Mexico                                        White alone   
11               New York                                        White alone   
12         North Carolina                                        White alone   
13           North Dakota                                        White alone   
14                   Ohio                                        White alone   
15               Oklahoma                                        White alone   
16                 Oregon                                        White alone   
17           Pennsylvania                                        White alone   
18           Rhode Island                                        White alone   
19         South Carolina                                        White alone   
20                 Kansas                                        White alone   
21              Tennessee                                        White alone   
22                  Texas                                        White alone   
23                Vermont                                        White alone   
24                   Utah                                        White alone   
25               Virginia                                        White alone   
26             Washington                                        White alone   
27          West Virginia                                        White alone   
28                Alabama                                        White alone   
29                 Alaska                                        White alone   
30                Arizona                                        White alone   
31               Arkansas                                        White alone   
32             California                                        White alone   
33               Colorado                                        White alone   
34               Delaware                                        White alone   
35            Connecticut                                        White alone   
36   District of Columbia                                        White alone   
37                Florida                                        White alone   
38                Georgia                                        White alone   
39                 Hawaii                                        White alone   
40                  Idaho                                        White alone   
41               Illinois                                        White alone   
42                Indiana                                        White alone   
43                   Iowa                                        White alone   
44               Michigan                                        White alone   
45              Minnesota                                        White alone   
46          Massachusetts                                        White alone   
47               Kentucky                                        White alone   
48              Louisiana                                        White alone   
49                  M

In [ ]:
# Call 5: demographics for selected populations of women by state for 2019

# Race = White 
url_1 = 'https://api.census.gov/data/2019/acs/acs1/spp?'\
          'get=NAME,POPGROUP_LABEL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=002&key={0}'\
          .format(census_api_key)

# Race = Black 
url_2 = 'https://api.census.gov/data/2019/acs/acs1/spp?'\
          'get=NAME,POPGROUP_LABEL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=004&key={0}'\
          .format(census_api_key)

# Race = American Indian and Alaska Native alone   
url_3 = 'https://api.census.gov/data/2019/acs/acs1/spp?'\
          'get=NAME,POPGROUP_LABEL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=006&key={0}'\
          .format(census_api_key)

# Race = Asian 
url_4 = 'https://api.census.gov/data/2019/acs/acs1/spp?'\
          'get=NAME,POPGROUP_LABEL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=012&key={0}'\
          .format(census_api_key)

# Race = Native Hawaiian and other Pacific Islander alone 
url_5 = 'https://api.census.gov/data/2019/acs/acs1/spp?'\
          'get=NAME,POPGROUP_LABEL,S0201_026E,S0201_028E,'\
          'S0201_035E,S0201_037E,S0201_072E,S0201_073E,'\
          'S0201_074E,S0201_075E,S0201_076E,S0201_077E,'\
          'S0201_090E,S0201_098E,S0201_101E,S0201_103E,'\
          'S0201_104E,S0201_127E,S0201_129E,S0201_130E,'\
          'S0201_132E,S0201_133E,S0201_135E,S0201_136E,'\
          'S0201_138E,S0201_162E,S0201_164E,S0201_165E,'\
          'S0201_166E,S0201_227E,S0201_231E,S0201_239E,'\
          'S0201_241E,S0201_242E,S0201_243E,S0201_244E,'\
          'S0201_245E,S0201_249E,S0201_250E,S0201_252E,'\
          'S0201_253E&for=state:*&POPGROUP=050&key={0}'\
          .format(census_api_key)

urls = [url_1,url_2,url_3,url_4,url_5]

dfs = []
for url in urls:
    try:
        response = requests.get(url)
        response.raise_for_status()
    except requests.exceptions.RequestException as e:
        print(e, file=sys.stderr)
    cols = response.json()[0]
    recs = response.json()[1:]
    data = pd.DataFrame(recs, columns=cols)
    dfs.append(data)
    
data_2019 = pd.concat(dfs, ignore_index=True)
data_2019['year'] = 2019
data_2019.rename(columns={'POPGROUP_LABEL':'RACE'},inplace= True)
data_2019

NAME                                               RACE  \
0             Mississippi                                        White alone   
1                Missouri                                        White alone   
2                 Montana                                        White alone   
3                Nebraska                                        White alone   
4                  Nevada                                        White alone   
5           New Hampshire                                        White alone   
6                New York                                        White alone   
7                Oklahoma                                        White alone   
8            Pennsylvania                                        White alone   
9            Rhode Island                                        White alone   
10         South Carolina                                        White alone   
11           South Dakota                                        White alone   
12              Tennessee                                        White alone   
13                  Texas                                        White alone   
14                Vermont                                        White alone   
15                   Utah                                        White alone   
16               Virginia                                        White alone   
17          West Virginia                                        White alone   
18              Wisconsin                                        White alone   
19                  Idaho                                        White alone   
20               Illinois                                        White alone   
21                   Iowa                                        White alone   
22                 Kansas                                        White alone   
23               Kentucky                                        White alone   
24                  Maine                                        White alone   
25               Maryland                                        White alone   
26          Massachusetts                                        White alone   
27              Minnesota                                        White alone   
28                Alabama                                        White alone   
29                Arizona                                        White alone   
30               Colorado                                        White alone   
31               Delaware                                        White alone   
32   District of Columbia                                        White alone   
33             California                                        White alone   
34             New Jersey                                        White alone   
35             New Mexico                                        White alone   
36         North Carolina                                        White alone   
37           North Dakota                                        White alone   
38                   Ohio                                        White alone   
39                 Oregon                                        White alone   
40             Washington                                        White alone   
41                Wyoming                                        White alone   
42                Georgia                                        White alone   
43                 Hawaii                                        White alone   
44                Indiana                                        White alone   
45              Louisiana                                        White alone   
46               Michigan                                        White alone   
47            Connecticut                                        White alone   
48                Florida                                        White alone   
49                 Al

In [ ]:
data = pd.concat([data_2015,data_2016,data_2017,data_2018,data_2019], ignore_index=True)
data

NAME                                               RACE  \
0             Mississippi                                        White alone   
1                Missouri                                        White alone   
2                 Montana                                        White alone   
3                Nebraska                                        White alone   
4                  Nevada                                        White alone   
5           New Hampshire                                        White alone   
6              New Jersey                                        White alone   
7              New Mexico                                        White alone   
8                New York                                        White alone   
9          North Carolina                                        White alone   
10           North Dakota                                        White alone   
11                   Ohio                                        White alone   
12               Oklahoma                                        White alone   
13                 Oregon                                        White alone   
14         South Carolina                                        White alone   
15           South Dakota                                        White alone   
16              Tennessee                                        White alone   
17           Pennsylvania                                        White alone   
18           Rhode Island                                        White alone   
19                   Utah                                        White alone   
20                  Texas                                        White alone   
21                Vermont                                        White alone   
22               Virginia                                        White alone   
23             Washington                                        White alone   
24          West Virginia                                        White alone   
25              Wisconsin                                        White alone   
26                Arizona                                        White alone   
27                Wyoming                                        White alone   
28                Alabama                                        White alone   
29                 Alaska                                        White alone   
30               Arkansas                                        White alone   
31                 Hawaii                                        White alone   
32                Georgia                                        White alone   
33             California                                        White alone   
34               Colorado                                        White alone   
35               Delaware                                        White alone   
36            Connecticut                                        White alone   
37   District of Columbia                                        White alone   
38                Florida                                        White alone   
39                  Idaho                                        White alone   
40               Illinois                                        White alone   
41                Indiana                                        White alone   
42                   Iowa                                        White alone   
43                 Kansas                                        White alone   
44               Kentucky                                        White alone   
45              Louisiana                                        White alone   
46                  Maine                                        White alone   
47               Michigan                                        White alone   
48              Minnesota                                        White alone   
49               Mary

In [ ]:
data.shape

(681, 44)

### Dealing with the classifying fields, i.e., year, state, state code, race and race code

In [ ]:
# renaming the variables 
data.rename(columns={'state':'state_code',
                     'NAME':'state',
                     'RACE':'race',
                     'POPGROUP':'race_code'},
            inplace= True)

# assigning the correct data type to the variables
data['state'] = data['state'].astype('category')
data['race'] = data['race'].astype('category')
data['race_code'] = data['race_code'].astype('category')
data['state_code'] = data['state_code'].astype('category')
data['year'] = data['year'].astype('category')

# fixing the race column categories
to_replace = {' alone':'',
              ' \(300, A01-Z99\)':'',
              ' \(400-499\)':'',
              ' \(500-599\)':''}  
for k, v in to_replace.items():
    data['race'] = data['race'].str.replace(k, v, regex=True)
    
data['race'] = data['race'].apply(lambda x : 'Native Hawaiian and Other Pacific Islander' 
                                  if x == ('Asian') 
                                  else x)
data['race'] = data['race'].str.replace('Native Hawaiian and Other Pacific Islander',
                                        'Asian or Pacific Islander')
data['race'] = data['race'].str.replace('American Indian and Alaska Native',
                                        'American Indian or Alaska Native')
data.shape

(681, 44)

### Dealing with population data (S0201_026 to S0201_037)

In [ ]:
# renaming the variables 
data.rename(columns={'S0201_026E':'pop_over18',
                     'S0201_028E':'fper_over18',
                     'S0201_035E':'pop_over65',
                     'S0201_037E':'fper_over65'},
            inplace= True)

# assigning the correct data type to the variables
data['pop_over18'] = data['pop_over18'].astype('int64')
data['fper_over18'] = data['fper_over18'].astype('float')
data['pop_over65'] = data['pop_over65'].astype('int64')
data['fper_over65'] = data['fper_over65'].astype('float')

# checking for negative values
(data[['pop_over18',
       'fper_over18',
       'pop_over65',
       'fper_over65']] < 0).any().any()

False

In [ ]:
# calculating actual numbers from percentages

data['fpop_over18'] = (data['pop_over18'] * (data['fper_over18'] / 100)).astype('int64')
data['fpop_over65'] = (data['pop_over65'] * (data['fper_over65'] / 100)).astype('int64')
data['fpop'] = (data['fpop_over18'] - data['fpop_over65']).astype(int)

data.shape

(681, 47)

### Dealing with marital status fields (S0201_072 to S0201_072)

In [ ]:
# renaming the variables 
data.rename(columns={'S0201_072E':'fpop_over15',
                     'S0201_073E':'per_married',
                     'S0201_074E':'per_widowed',
                     'S0201_075E':'per_divorced',
                     'S0201_076E':'per_separated',
                     'S0201_077E':'per_never_mar'},
            inplace= True)

# assigning the correct data type to the variables
data['fpop_over15'] = data['fpop_over15'].astype('int64')
data['per_married'] = data['per_married'].astype('float')
data['per_widowed'] = data['per_widowed'].astype('float')
data['per_divorced'] = data['per_divorced'].astype('float')
data['per_separated'] = data['per_separated'].astype('float')
data['per_never_mar'] = data['per_never_mar'].astype('float')

# checking for negative values
(data[['fpop_over15',
       'per_married',
       'per_widowed',
       'per_divorced',
       'per_separated',
       'per_never_mar']] < 0).any().any()

False

In [ ]:
# calculating actual numbers from percentages

data['pop_married'] = (data['fpop_over15'] * (data['per_married'] / 100)).astype('int64')
data['pop_widowed'] = (data['fpop_over15'] * (data['per_widowed'] / 100)).astype('int64')
data['pop_divorced'] = (data['fpop_over15'] * (data['per_divorced'] / 100)).astype('int64')
data['pop_separated'] = (data['fpop_over15'] * (data['per_separated'] / 100)).astype('int64')
data['pop_never_mar'] = (data['fpop_over15'] * (data['per_never_mar'] / 100)).astype('int64')

data.shape

(681, 52)

### Dealing with educational attainment fields (S0201_090, S0201_098 & S0201_101)

In [ ]:
# renaming the variables 
data.rename(columns={'S0201_090E':'pop_over25',
                     'S0201_098E':'fper_hs_diploma',
                     'S0201_101E':'fper_higher_ed'},
            inplace= True)

# assigning the correct data type to the variables
data['pop_over25'] = data['pop_over25'].astype('int64')
data['fper_hs_diploma'] = data['fper_hs_diploma'].astype('float')
data['fper_higher_ed'] = data['fper_higher_ed'].astype('float')

# checking for negative values
(data[['pop_over25',
       'fper_hs_diploma',
       'fper_higher_ed']] < 0).any().any()

False

In [ ]:
# calculating actual numbers from percentages

data['pop_hs_diploma'] = (data['pop_over25'] * (data['fper_hs_diploma'] / 100)).astype('int64')
data['pop_higher_ed'] = (data['pop_over25'] * (data['fper_higher_ed'] / 100)).astype('int64')

data.shape

(681, 54)

### Dealing with fertility fields (S0201_103 & S0201_104)

In [ ]:
# renaming the variables 
data.rename(columns={'S0201_103E':'fertility',
                     'S0201_104E':'fertility_um'},
            inplace= True)

# assigning the correct data type to the variables
data['fertility'] = data['fertility'].astype('int64')
data['fertility_um'] = data['fertility_um'].astype('int64')

# checking for negative values
(data[['fertility',
       'fertility_um']] < 0).any().any()

True

In [ ]:
# converting negative population values to NaN
data['fertility'] = data['fertility'].apply(lambda x : x if x > 0 else np.nan)
data['fertility_um'] = data['fertility_um'].apply(lambda x : x if x > 0 else np.nan)

(data[['fertility',
       'fertility_um']] < 0).any().any()

False

In [ ]:
# feature engineering
data['fertility_ma'] = data['fertility'] - data['fertility_um']

data.shape

(681, 55)

### Dealing with citizenship status fields (S0201_127 to S0201_138)

In [ ]:
# renaming the variables 
data.rename(columns={'S0201_127E':'native_pop',
                     'S0201_129E':'native_fper',
                     'S0201_130E':'foreign_pop',
                     'S0201_132E':'foreign_fper',
                     'S0201_133E':'foreign_cit_pop',
                     'S0201_135E':'foreign_cit_fper',
                     'S0201_136E':'foreign_imm_pop',
                     'S0201_138E':'foreign_imm_fper'},
            inplace= True)

# assigning the correct data type to the variables
data['native_pop'] = data['native_pop'].astype('int64')
data['native_fper'] = data['native_fper'].astype('float')
data['foreign_pop'] = data['foreign_pop'].astype('int64')
data['foreign_fper'] = data['foreign_fper'].astype('float')
data['foreign_cit_pop'] = data['foreign_cit_pop'].astype('int64')
data['foreign_cit_fper'] = data['foreign_cit_fper'].astype('float')
data['foreign_imm_pop'] = data['foreign_imm_pop'].astype('int64')
data['foreign_imm_fper'] = data['foreign_imm_fper'].astype('float')

# checking for negative values
(data[['native_pop','native_fper',
       'foreign_pop','foreign_fper',
       'foreign_cit_pop','foreign_cit_fper',
       'foreign_imm_pop','foreign_imm_fper']] < 0).any().any()

True

In [ ]:
# converting negative population values to NaN
data['native_pop'] = data['native_pop'].apply(lambda x : x if x > 0 else np.nan)
data['native_fper'] = data['native_fper'].apply(lambda x : x if x > 0 else np.nan)
data['foreign_pop'] = data['foreign_pop'].apply(lambda x : x if x > 0 else np.nan)
data['foreign_fper'] = data['foreign_fper'].apply(lambda x : x if x > 0 else np.nan)
data['foreign_cit_pop'] = data['foreign_cit_pop'].apply(lambda x : x if x > 0 else np.nan)
data['foreign_cit_fper'] = data['foreign_cit_fper'].apply(lambda x : x if x > 0 else np.nan)
data['foreign_imm_pop'] = data['foreign_imm_pop'].apply(lambda x : x if x > 0 else np.nan)
data['foreign_imm_fper'] = data['foreign_imm_fper'].apply(lambda x : x if x > 0 else np.nan)

(data[['native_pop','native_fper',
       'foreign_pop','foreign_fper',
       'foreign_cit_pop','foreign_cit_fper',
       'foreign_imm_pop','foreign_cit_fper']] < 0).any().any()

False

In [ ]:
# calculating actual numbers from percentages
data['native_fpop'] = (data['native_pop'] * (data['native_fper'] / 100)).astype('int64')
data['foreign_fpop'] = (data['foreign_pop'] * (data['foreign_fper'] / 100)).astype('float')
data['foreign_cit_fpop'] = (data['foreign_cit_pop'] * (data['foreign_cit_fper'] / 100)).astype('float')
data['foreign_imm_fpop'] = (data['foreign_imm_pop'] * (data['foreign_imm_fper'] / 100)).astype('float')

data.shape

(681, 59)

### Dealing with labor fields (S0201_162 to S0201_166)

In [ ]:
# renaming the variables 
data.rename(columns={'S0201_162E':'pop_over16',
                     'S0201_164E':'per_labor_force_f',
                     'S0201_165E':'per_employed_f',
                     'S0201_166E':'per_unemployed_f'},
            inplace= True)

# assigning the correct data type to the variables
data['pop_over16'] = data['pop_over16'].astype('int64')
data['per_labor_force_f'] = data['per_labor_force_f'].astype('float')
data['per_employed_f'] = data['per_employed_f'].astype('float')
data['per_unemployed_f'] = data['per_unemployed_f'].astype('float')

# checking for negative values
(data[['pop_over16',
       'per_labor_force_f',
       'per_employed_f',
       'per_unemployed_f']] < 0).any().any()

False

In [ ]:
# calculating actual numbers from percentages
data['labor_force_f'] = (data['pop_over16'] * (data['per_labor_force_f'] / 100)).astype('int64')
data['employed_f'] = (data['labor_force_f'] * (data['per_employed_f'] / 100)).astype('int64')
data['unemployed_f'] = (data['labor_force_f'] * (data['per_unemployed_f'] / 100)).astype('int64')

data.shape

(681, 62)

### Dealing with income fields (S0201_227 to S0201_241)

In [ ]:
# renaming the variables 
data.rename(columns={'S0201_227E':'fam_inc_mc',
                     'S0201_231E':'fam_inc_um',
                     'S0201_239E':'fmean_inc',
                     'S0201_241E':'fmed_inc'},
            inplace= True)

# assigning the correct data type to the variables
data['fam_inc_mc'] = data['fam_inc_mc'].astype('float')
data['fam_inc_um'] = data['fam_inc_um'].astype('float')
data['fmean_inc'] = data['fmean_inc'].astype('float')
data['fmed_inc'] = data['fmed_inc'].astype('float')

# checking for negative values
(data[['fam_inc_mc',
       'fam_inc_um',
       'fmean_inc',
       'fmed_inc']] < 0).any().any()

True

In [ ]:
# converting negative data values to NaN
data['fam_inc_mc'] = data['fam_inc_mc'].apply(lambda x : x if x > 0 else np.nan)
data['fam_inc_um'] = data['fam_inc_um'].apply(lambda x : x if x > 0 else np.nan)
data['fmean_inc'] = data['fmean_inc'].apply(lambda x : x if x > 0 else np.nan)
data['fmed_inc'] = data['fmed_inc'].apply(lambda x : x if x > 0 else np.nan)

(data[['fam_inc_mc',
       'fam_inc_um',
       'fmean_inc',
       'fmed_inc']] < 0).any().any()

False

### Dealing with insurance fields (S0201_242 to S0201_245)

In [ ]:
# renaming the variables 
data.rename(columns={'S0201_242E':'population',
                     'S0201_243E':'insur_pri_per',
                     'S0201_244E':'insur_pub_per',
                     'S0201_245E':'insur_non_per'},
            inplace= True)

# assigning the correct data type to the variables
data['population'] = data['population'].astype('int64')
data['insur_pri_per'] = data['insur_pri_per'].astype('float')
data['insur_pub_per'] = data['insur_pub_per'].astype('float')
data['insur_non_per'] = data['insur_non_per'].astype('float')

# checking for negative values
(data[['population',
       'insur_pri_per',
       'insur_pub_per',
       'insur_non_per']] < 0).any().any()

False

In [ ]:
# calculating actual numbers from percentages
# Assuming women make up 51.3% of the population on average (Data taken from the census db)
data['insur_pri_pop'] = (data['population'] * 0.513 * (data['insur_pri_per'] / 100)).astype('int64')
data['insur_pub_pop'] = (data['population'] * 0.513 * (data['insur_pub_per'] / 100)).astype('int64')
data['insur_non_pop'] = (data['population'] * 0.513 * (data['insur_non_per'] / 100)).astype('int64')

data.shape

(681, 65)

### Dealing with poverty rate fields (S0201_249 to S0201_253)

In [ ]:
# renaming the variables 
data.rename(columns={'S0201_249E':'pr_marr',
                     'S0201_250E':'pr_marr_kid',
                     'S0201_252E':'pr_unmarr',
                     'S0201_253E':'pr_unmarr_kid'},
            inplace= True)

# assigning the correct data type to thevariables
data['pr_marr'] = data['pr_marr'].astype('float')
data['pr_marr_kid'] = data['pr_marr_kid'].astype('float')
data['pr_unmarr'] = data['pr_unmarr'].astype('float')
data['pr_unmarr_kid'] = data['pr_unmarr_kid'].astype('float')

# checking for negative values
(data[['pr_marr',
       'pr_marr_kid',
       'pr_unmarr',
       'pr_unmarr_kid']] < 0).any().any()

True

In [ ]:
# converting negative data values to zero
data['pr_marr'] = data['pr_marr'].apply(lambda x : x if x > 0 else np.nan)
data['pr_marr_kid'] = data['pr_marr_kid'].apply(lambda x : x if x > 0 else np.nan)
data['pr_unmarr'] = data['pr_unmarr'].apply(lambda x : x if x > 0 else 0)
data['pr_unmarr_kid'] = data['pr_unmarr_kid'].apply(lambda x : x if x > 0 else np.nan)

(data[['pr_marr',
       'pr_marr_kid',
       'pr_unmarr',
       'pr_unmarr_kid']] < 0).any().any()

False

In [ ]:
data.shape

(681, 65)

In [ ]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 681 entries, 0 to 680
Data columns (total 65 columns):
 #   Column             Non-Null Count  Dtype   
---  ------             --------------  -----   
 0   state              681 non-null    category
 1   race               681 non-null    object  
 2   pop_over18         681 non-null    int64   
 3   fper_over18        681 non-null    float64 
 4   pop_over65         681 non-null    int64   
 5   fper_over65        681 non-null    float64 
 6   fpop_over15        681 non-null    int64   
 7   per_married        681 non-null    float64 
 8   per_widowed        681 non-null    float64 
 9   per_divorced       681 non-null    float64 
 10  per_separated      681 non-null    float64 
 11  per_never_mar      681 non-null    float64 
 12  pop_over25         681 non-null    int64   
 13  fper_hs_diploma    681 non-null    float64 
 14  fper_higher_ed     681 non-null    float64 
 15  fertility          681 non-null    int64   
 16  fertilit

### Selecting required fields

||Variable Name|Description|
|:---:|:-----:|:-------------:|
|01|year|Census year|
|02|state|U.S. state name|
|03|race|Race|
|04|married|Population of women, 15 and over, that are currently married|
|05|widowed|Population of women, 15 and over, that are widowed|
|06|divorced|Population of women, 15 and over, that are divorced|
|07|separated|Population of women, 15 and over, that are separated|
|08|never_mar|Population of women, 15 and over, that have never been married|
|09|hs_diploma|Population of women, 25 and over, that hold a high school diploma|
|10|higher_ed|Population of women, 25 and over, that have a higher education|
|11|fertile_marr|Population of women, between 15 and 50, that gave birth and are married|
|12|fertile_unma|Population of women, between 15 and 50, that gave birth and are unmarried|
|13|us_native|Population of women that are native-born U.S. citizens|
|14|foreign_cit|Population of women that are foreign-born U.S. citizens|
|15|foreign_imm|Population of women that are foreign-born U.S. immigrants|
|16|employed|Population of women, 16 and over, that are employed|
|17|unemployed|Population of women, 16 and over, that are unemployed|
|18|single_inc|Median income of single women|
|19|marr_fam_inc|Income of families with a married couple|
|20|unma_fam_inc|Income of families with an unmarried female homeowner|
|21|insured_priv|Population of women that are privately insured|
|22|insured_publ|Population of women that are publicly insured|
|23|insured_none|Population of women that are not insured|
|24|poverty_marr|Poverty rate of married couples|
|25|poverty_marr_kids|Poverty rate of married couples with kids under 18|
|26|poverty_unma|Poverty rate of unmarried women|
|27|poverty_unma_kids|Poverty rate of unmarried women with kids under 18|

In [ ]:
data_2 = data[['year','state','race',
               'pop_married','pop_widowed','pop_divorced','pop_separated','pop_never_mar',
               'pop_hs_diploma','pop_higher_ed',
               'fertility_ma','fertility_um',
               'native_fpop','foreign_cit_fpop','foreign_imm_fpop',
               'employed_f','unemployed_f',
               'fmed_inc','fam_inc_mc','fam_inc_um',
               'insur_pri_pop','insur_pub_pop','insur_non_pop',
               'pr_marr','pr_marr_kid','pr_unmarr','pr_unmarr_kid']].copy()

data_2.rename(columns={'pop_married':'married',
                       'pop_widowed':'widowed',
                       'pop_divorced':'divorced',
                       'pop_separated':'separated',
                       'pop_never_mar':'never_mar',
                       'pop_hs_diploma':'hs_diploma',
                       'pop_higher_ed':'higher_ed',
                       'fertility_ma':'fertile_marr',
                       'fertility_um':'fertile_unma',
                       'native_fpop':'us_native',
                       'foreign_cit_fpop':'foreign_cit',
                       'foreign_imm_fpop':'foreign_imm',
                       'employed_f':'employed',
                       'unemployed_f':'unemployed',
                       'fmed_inc':'single_inc',
                       'fam_inc_mc':'marr_fam_inc',
                       'fam_inc_um':'unma_fam_inc',
                       'insur_pri_pop':'insured_priv',
                       'insur_pub_pop':'insured_publ',
                       'insur_non_pop':'insured_none',
                       'pr_marr':'poverty_marr',
                       'pr_marr_kid':'poverty_marr_kids',
                       'pr_unmarr':'poverty_unma',
                       'pr_unmarr_kid':'poverty_unma_kids'},
              inplace=True)
data_2

year                 state                              race  married  \
0    2015           Mississippi                             White   390060   
1    2015              Missouri                             White  1070470   
2    2015               Montana                             White   198080   
3    2015              Nebraska                             White   358660   
4    2015                Nevada                             White   369237   
5    2015         New Hampshire                             White   269012   
6    2015            New Jersey                             White  1282966   
7    2015            New Mexico                             White   296802   
8    2015              New York                             White  2491891   
9    2015        North Carolina                             White  1535625   
10   2015          North Dakota                             White   143565   
11   2015                  Ohio                             White  2008143   
12   2015              Oklahoma                             White   616209   
13   2015                Oregon                             White   699479   
14   2015        South Carolina                             White   733436   
15   2015          South Dakota                             White   164088   
16   2015             Tennessee                             White  1113168   
17   2015          Pennsylvania                             White  2218854   
18   2015          Rhode Island                             White   162731   
19   2015                  Utah                             White   549565   
20   2015                 Texas                             White  4076091   
21   2015               Vermont                             White   124575   
22   2015              Virginia                             White  1241780   
23   2015            Washington                             White  1166260   
24   2015         West Virginia                             White   358722   
25   2015             Wisconsin                             White  1087536   
26   2015               Arizona                             White  1041146   
27   2015               Wyoming                             White   115766   
28   2015               Alabama                             White   738116   
29   2015                Alaska                             White    98037   
30   2015              Arkansas                             White   511161   
31   2015                Hawaii                             White    75577   
32   2015               Georgia                             White  1329977   
33   2015            California                             White  4512396   
34   2015              Colorado                             White   974179   
35   2015              Delaware                             White   138516   
36   2015           Connecticut                             White   576882   
37   2015  District of Columbia                             White    43406   
38   2015               Florida                             White  3119228   
39   2015                 Idaho                             White   319513   
40   2015              Illinois                             White  1940878   
41   2015               Indiana                             White  1154084   
42   2015                  Iowa                             White   612273   
43   2015                Kansas                             White   527036   
44   2015              Kentucky                             White   817231   
45   2015             Louisiana                             White   607669   
46   2015                 Maine                             White   267184   
47   2015              Michigan                             White  1678674   
48   2015             Minnesota                             White  1026176   
49   2015              Maryland                             White   744175   
50   2015         Massachus

In [ ]:
data_2.shape

(681, 27)

### Dealing with the Asian/Pacific Islander Variables

Since we changed the labelling in the race column, the data currently has two records for the Asian/Pacific Islander race category, so we need to deal with this before getting averaging our data over the last five years

In [ ]:
data_2.columns

Index(['year', 'state', 'race', 'married', 'widowed', 'divorced', 'separated',
       'never_mar', 'hs_diploma', 'higher_ed', 'fertile_marr', 'fertile_unma',
       'us_native', 'foreign_cit', 'foreign_imm', 'employed', 'unemployed',
       'single_inc', 'marr_fam_inc', 'unma_fam_inc', 'insured_priv',
       'insured_publ', 'insured_none', 'poverty_marr', 'poverty_marr_kids',
       'poverty_unma', 'poverty_unma_kids'],
      dtype='object')

In [ ]:
data_3 = data_2.groupby(['year',
                        'state',
                        'race']).agg({'married':'sum', 
                                     'widowed':'sum', 
                                     'divorced':'sum', 
                                     'separated':'sum',
                                     'never_mar':'sum', 
                                     'hs_diploma':'sum', 
                                     'higher_ed':'sum', 
                                     'fertile_marr':'sum', 
                                     'fertile_unma':'sum',
                                     'us_native':'sum', 
                                     'foreign_cit':'sum', 
                                     'foreign_imm':'sum', 
                                     'employed':'sum', 
                                     'unemployed':'sum',
                                     'single_inc':'mean', 
                                     'marr_fam_inc':'mean', 
                                     'unma_fam_inc':'mean', 
                                     'insured_priv':'sum',
                                     'insured_publ':'sum', 
                                     'insured_none':'sum', 
                                     'poverty_marr':'mean', 
                                     'poverty_marr_kids':'mean',
                                     'poverty_unma':'mean', 
                                     'poverty_unma_kids':'mean'}).copy().reset_index()
data_3

year                 state                              race  married  \
0     2015               Alabama  American Indian or Alaska Native        0   
1     2015               Alabama         Asian or Pacific Islander        0   
2     2015               Alabama         Black or African American   141206   
3     2015               Alabama                             White   738116   
4     2015                Alaska  American Indian or Alaska Native    13477   
5     2015                Alaska         Asian or Pacific Islander        0   
6     2015                Alaska         Black or African American        0   
7     2015                Alaska                             White    98037   
8     2015               Arizona  American Indian or Alaska Native    37363   
9     2015               Arizona         Asian or Pacific Islander    60645   
10    2015               Arizona         Black or African American    31898   
11    2015               Arizona                             White  1041146   
12    2015              Arkansas  American Indian or Alaska Native        0   
13    2015              Arkansas         Asian or Pacific Islander        0   
14    2015              Arkansas         Black or African American    48684   
15    2015              Arkansas                             White   511161   
16    2015            California  American Indian or Alaska Native    41161   
17    2015            California         Asian or Pacific Islander  1409190   
18    2015            California         Black or African American   230499   
19    2015            California                             White  4512396   
20    2015              Colorado  American Indian or Alaska Native        0   
21    2015              Colorado         Asian or Pacific Islander    42139   
22    2015              Colorado         Black or African American    25083   
23    2015              Colorado                             White   974179   
24    2015           Connecticut  American Indian or Alaska Native        0   
25    2015           Connecticut         Asian or Pacific Islander    39953   
26    2015           Connecticut         Black or African American    41082   
27    2015           Connecticut                             White   576882   
28    2015              Delaware  American Indian or Alaska Native        0   
29    2015              Delaware         Asian or Pacific Islander        0   
30    2015              Delaware         Black or African American    25434   
31    2015              Delaware                             White   138516   
32    2015  District of Columbia  American Indian or Alaska Native        0   
33    2015  District of Columbia         Asian or Pacific Islander        0   
34    2015  District of Columbia         Black or African American    26637   
35    2015  District of Columbia                             White    43406   
36    2015               Florida  American Indian or Alaska Native        0   
37    2015               Florida         Asian or Pacific Islander   149234   
38    2015               Florida         Black or African American   368353   
39    2015               Florida                             White  3119228   
40    2015               Georgia  American Indian or Alaska Native        0   
41    2015               Georgia         Asian or Pacific Islander   101955   
42    2015               Georgia         Black or African American   381601   
43    2015               Georgia                             White  1329977   
44    2015                Hawaii  American Indian or Alaska Native        0   
45    2015                Hawaii         Asian or Pacific Islander   153051   
46    2015                Hawaii         Black or African American        0   
47    2015                Hawaii                             White    75577   
48    2015                 Idaho  American Indian or Alaska Native        0   
49    2015                 Idaho         Asian or Pacifi

### Averaging socioeconmic data over five years to be consistent with the mortality data collected from the CDC

In [ ]:
df2 = data_3.groupby(['state','race']).mean().copy().reset_index()
df2

state                              race    married  \
0                 Alabama  American Indian or Alaska Native        0.0   
1                 Alabama         Asian or Pacific Islander    14966.4   
2                 Alabama         Black or African American   146081.6   
3                 Alabama                             White   745617.2   
4                  Alaska  American Indian or Alaska Native    14106.6   
5                  Alaska         Asian or Pacific Islander        0.0   
6                  Alaska         Black or African American        0.0   
7                  Alaska                             White    99149.2   
8                 Arizona  American Indian or Alaska Native    36355.2   
9                 Arizona         Asian or Pacific Islander    62928.6   
10                Arizona         Black or African American    35055.8   
11                Arizona                             White  1092100.6   
12               Arkansas  American Indian or Alaska Native        0.0   
13               Arkansas         Asian or Pacific Islander        0.0   
14               Arkansas         Black or African American    49710.0   
15               Arkansas                             White   500296.6   
16             California  American Indian or Alaska Native    46188.6   
17             California         Asian or Pacific Islander  1465593.4   
18             California         Black or African American   236572.4   
19             California                             White  4482662.6   
20               Colorado  American Indian or Alaska Native        0.0   
21               Colorado         Asian or Pacific Islander    47810.4   
22               Colorado         Black or African American    28076.6   
23               Colorado                             White   997545.6   
24            Connecticut  American Indian or Alaska Native        0.0   
25            Connecticut         Asian or Pacific Islander    44025.2   
26            Connecticut         Black or African American    42915.0   
27            Connecticut                             White   573411.0   
28               Delaware  American Indian or Alaska Native        0.0   
29               Delaware         Asian or Pacific Islander        0.0   
30               Delaware         Black or African American    25224.8   
31               Delaware                             White   143006.2   
32   District of Columbia  American Indian or Alaska Native        0.0   
33   District of Columbia         Asian or Pacific Islander        0.0   
34   District of Columbia         Black or African American    24204.2   
35   District of Columbia                             White    45781.4   
36                Florida  American Indian or Alaska Native        0.0   
37                Florida         Asian or Pacific Islander   158660.4   
38                Florida         Black or African American   388447.8   
39                Florida                             White  3225876.4   
40                Georgia  American Indian or Alaska Native        0.0   
41                Georgia         Asian or Pacific Islander   110345.8   
42                Georgia         Black or African American   391664.4   
43                Georgia                             White  1345133.2   
44                 Hawaii  American Indian or Alaska Native        0.0   
45                 Hawaii         Asian or Pacific Islander   158171.4   
46                 Hawaii         Black or African American        0.0   
47                 Hawaii                             White    75225.6   
48                  Idaho  American Indian or Alaska Native        0.0   
49                  Idaho         Asian or Pacific Islander        0.0   
50                  Idaho         Black or African American        0.0   
51                  Idaho                             White   335300.6   
52               Illinois  American Indian or Alaska Native        0.0   
53               Illinoi

In [ ]:
df2.shape

(204, 26)

In [ ]:
df2.to_csv('socioecon_data.csv', index=False)

## Concatenating the datasets

### Making sure the two datasets are organized in the same manner

In [ ]:
df1.head()

state                              race  deaths  crude_rate  age_adj_rate
0  Alabama  American Indian or Alaska Native     NaN         NaN           NaN
1  Alabama         Asian or Pacific Islander     NaN         NaN           NaN
2  Alabama         Black or African American   124.0         1.5           1.6
3  Alabama                             White   137.0         0.7           0.8
4   Alaska  American Indian or Alaska Native    10.0         NaN           NaN

In [ ]:
df1.shape

(204, 5)

In [ ]:
df2.head()

state                              race   married   widowed  divorced  \
0  Alabama  American Indian or Alaska Native       0.0       0.0       0.0   
1  Alabama         Asian or Pacific Islander   14966.4    1240.6    1491.8   
2  Alabama         Black or African American  146081.6   52971.2   78583.0   
3  Alabama                             White  745617.2  159695.6  188400.0   
4   Alaska  American Indian or Alaska Native   14106.6    2964.8    4743.4   

   separated  never_mar  hs_diploma  higher_ed  fertile_marr  fertile_unma  \
0        0.0        0.0         0.0        0.0           0.0           0.0   
1      221.6     5381.6     30357.0    16859.6           0.0           0.0   
2    25346.6   262989.8    709623.4   170978.8        5364.4       14404.4   
3    27844.6   298651.4   2077282.2   647509.6       26329.2       10057.2   
4     1448.0    17039.4     50817.0     5813.2         734.4        1297.6   

   us_native  foreign_cit  foreign_imm  employed  unemployed  single_inc  \
0        0.0       0.0000       0.0000       0.0         0.0         NaN   
1     7406.8   11826.5622    9618.2674    6117.0       260.8     44508.0   
2   689218.4    3093.0312    3306.8976  167061.0     16470.6     30560.0   
3  1657752.0   15132.3226   20417.5220  334003.4     16386.6     38105.4   
4    54243.4      92.6184       0.0000   10491.4      1870.2     41640.4   

   marr_fam_inc  unma_fam_inc  insured_priv  insured_publ  insured_none  \
0           NaN           NaN           0.0           0.0           0.0   
1       82042.5  41543.333333       21320.6        4844.2        2756.0   
2       41421.2  36678.000000      354856.6      296495.4       73927.2   
3       69768.2  46528.800000     1223167.8      575669.4      141657.8   
4       54406.6  36256.800000       16935.4       27496.8       14343.0   

   poverty_marr  poverty_marr_kids  poverty_unma  poverty_unma_kids  
0           NaN                NaN           NaN                NaN  
1          7.80              8.725        16.075              14.90  
2          7.54              9.220        38.980              50.12  
3          4.80              6.700        27.800              39.08  
4         11.40             16.020        29.840              36.00

In [ ]:
df2.shape

(204, 26)

In [ ]:
df3 = df1.merge(df2, how='inner', on=['state','race'])
df3

state                              race  deaths  \
0                 Alabama  American Indian or Alaska Native     NaN   
1                 Alabama         Asian or Pacific Islander     NaN   
2                 Alabama         Black or African American   124.0   
3                 Alabama                             White   137.0   
4                  Alaska  American Indian or Alaska Native    10.0   
5                  Alaska         Asian or Pacific Islander     NaN   
6                  Alaska         Black or African American     NaN   
7                  Alaska                             White     NaN   
8                 Arizona  American Indian or Alaska Native    31.0   
9                 Arizona         Asian or Pacific Islander     NaN   
10                Arizona         Black or African American    33.0   
11                Arizona                             White   176.0   
12               Arkansas  American Indian or Alaska Native     NaN   
13               Arkansas         Asian or Pacific Islander     NaN   
14               Arkansas         Black or African American    47.0   
15               Arkansas                             White    82.0   
16             California  American Indian or Alaska Native     NaN   
17             California         Asian or Pacific Islander    83.0   
18             California         Black or African American   115.0   
19             California                             White   472.0   
20               Colorado  American Indian or Alaska Native     NaN   
21               Colorado         Asian or Pacific Islander     NaN   
22               Colorado         Black or African American    17.0   
23               Colorado                             White   118.0   
24            Connecticut  American Indian or Alaska Native     NaN   
25            Connecticut         Asian or Pacific Islander     NaN   
26            Connecticut         Black or African American    18.0   
27            Connecticut                             White    40.0   
28               Delaware  American Indian or Alaska Native     NaN   
29               Delaware         Asian or Pacific Islander     NaN   
30               Delaware         Black or African American    15.0   
31               Delaware                             White    11.0   
32   District of Columbia  American Indian or Alaska Native     NaN   
33   District of Columbia         Asian or Pacific Islander     NaN   
34   District of Columbia         Black or African American    21.0   
35   District of Columbia                             White     NaN   
36                Florida  American Indian or Alaska Native     NaN   
37                Florida         Asian or Pacific Islander    11.0   
38                Florida         Black or African American   181.0   
39                Florida                             White   323.0   
40                Georgia  American Indian or Alaska Native     NaN   
41                Georgia         Asian or Pacific Islander    18.0   
42                Georgia         Black or African American   326.0   
43                Georgia                             White   274.0   
44                 Hawaii  American Indian or Alaska Native     NaN   
45                 Hawaii         Asian or Pacific Islander    25.0   
46                 Hawaii         Black or African American     NaN   
47                 Hawaii                             White     NaN   
48                  Idaho  American Indian or Alaska Native     NaN   
49                  Idaho         Asian or Pacific Islander     NaN   
50                  Idaho         Black or African American     NaN   
51                  Idaho                             White    48.0   
52               Illinois  American Indian or Alaska Native     NaN   
53               Illinois         Asian or Pacific Islander     NaN   
54               Illinois         Black or African American    92.0   
55               Illinois                   

In [ ]:
df3.shape

(204, 29)

### Assigning the right data types

In [ ]:
cats = ['state', 'race']

ints = ['married','widowed', 'divorced', 
        'separated','never_mar', 
        'hs_diploma', 'higher_ed', 
        'fertile_marr', 'fertile_unma',
        'us_native', 'foreign_cit', 
        'foreign_imm', 'employed', 
        'unemployed', 'insured_priv',
        'insured_publ', 'insured_none',
        'deaths']

flts = ['crude_rate', 'age_adj_rate',
        'single_inc', 'marr_fam_inc', 
        'unma_fam_inc','poverty_marr', 
        'poverty_marr_kids', 
        'poverty_unma',
        'poverty_unma_kids']

for col in df3.columns:
    if col in cats:
        df3[col] = df3[col].astype('category')
    elif col in ints:
        df3[col] = df3[col].round(decimals=0)
        df3[col] = df3[col].astype('Int64')
    else:
        df3[col] = df3[col].round(decimals=2)
        df3[col] = df3[col].astype('float')

df3.head()

state                              race  deaths  crude_rate  \
0  Alabama  American Indian or Alaska Native    <NA>         NaN   
1  Alabama         Asian or Pacific Islander    <NA>         NaN   
2  Alabama         Black or African American     124         1.5   
3  Alabama                             White     137         0.7   
4   Alaska  American Indian or Alaska Native      10         NaN   

   age_adj_rate  married  widowed  divorced  separated  never_mar  hs_diploma  \
0           NaN        0        0         0          0          0           0   
1           NaN    14966     1241      1492        222       5382       30357   
2           1.6   146082    52971     78583      25347     262990      709623   
3           0.8   745617   159696    188400      27845     298651     2077282   
4           NaN    14107     2965      4743       1448      17039       50817   

   higher_ed  fertile_marr  fertile_unma  us_native  foreign_cit  foreign_imm  \
0          0             0             0          0            0            0   
1      16860             0             0       7407        11827         9618   
2     170979          5364         14404     689218         3093         3307   
3     647510         26329         10057    1657752        15132        20418   
4       5813           734          1298      54243           93            0   

   employed  unemployed  single_inc  marr_fam_inc  unma_fam_inc  insured_priv  \
0         0           0         NaN           NaN           NaN             0   
1      6117         261     44508.0       82042.5      41543.33         21321   
2    167061       16471     30560.0       41421.2      36678.00        354857   
3    334003       16387     38105.4       69768.2      46528.80       1223168   
4     10491        1870     41640.4       54406.6      36256.80         16935   

   insured_publ  insured_none  poverty_marr  poverty_marr_kids  poverty_unma  \
0             0             0           NaN                NaN           NaN   
1          4844          2756          7.80               8.72         16.08   
2        296495         73927          7.54               9.22         38.98   
3        575669        141658          4.80               6.70         27.80   
4         27497         14343         11.40              16.02         29.84   

   poverty_unma_kids  
0                NaN  
1              14.90  
2              50.12  
3              39.08  
4              36.00

### Saving the data

In [ ]:
df3.to_csv("full_data.csv", index=False)

### Summary

This notebook was used to ingest pregnancy-related mortality and socioeconomic data for select female populations across the United States. 

Pregnancy-related mortality data was imported from the CDC Wonder database. Suppressed and unreliable values were converted to NaN values, and the records were grouped by state and race. 

Socioeconomic data was collected from the U.S. census database, grouped by year, state and race. Seven factors were taken into consideration - namely, marital status, educational attainment, fertility, citizenship, income, access to health insurance and poverty rate. For every variable, unrecorded values (negative values) were converted to NaN values, and actual population numbers were calculated from percentages. The data was then averaged over the five year period to be consistent with the mortality data.

Following data cleaning, the socioeconomic and mortality datasets were merged on the state and race columns.